In [1]:
import pandas as pd
import warnings

warnings.filterwarnings('ignore')

from keras.preprocessing.text import Tokenizer
from keras.preprocessing import sequence
from keras.layers import LSTM, Activation, Dense, Dropout, Input, Embedding
from keras.models import Model
from keras.callbacks import EarlyStopping

Using TensorFlow backend.


In [2]:
data = pd.read_csv('preprocessed_data.csv')

In [3]:
data.shape

(17897, 6)

In [4]:
data.head()

Id  Score                                              Title  \
0   260     49  adding scripting functionality .net applicatio...   
1   330     29  use nested class case? use nested class case? ...   
2   650     79  automatically update version number automatica...   
3   930     28  connect database loop recordset c connect data...   
4  1010     14  get value built, encoded viewstate? get value ...   

                                                Body      Tag  \
0  little game written c us database back-end. tr...   ['c#']   
1  working collection class used video playback r...  ['c++']   
2  would like version property application increm...   ['c#']   
3  what's simplest way connect query database set...   ['c#']   
4  need grab base64-encoded representation viewst...   ['c#']   

                                       modified_Body  
0  little game written c us database back-end. tr...  
1  working collection class used video playback r...  
2  would like version property application increm...  
3  what's simplest way connect query database set...  
4  need grab base64-encoded representation viewst...

In [5]:
new_data = data[['modified_Body', 'Tag']]

In [6]:
new_data.head()

modified_Body      Tag
0  little game written c us database back-end. tr...   ['c#']
1  working collection class used video playback r...  ['c++']
2  would like version property application increm...   ['c#']
3  what's simplest way connect query database set...   ['c#']
4  need grab base64-encoded representation viewst...   ['c#']

In [7]:
X = new_data['modified_Body']

In [8]:
from sklearn.preprocessing import MultiLabelBinarizer


y = new_data['Tag']

multilabel_binarizer = MultiLabelBinarizer()
y_bin = multilabel_binarizer.fit_transform(y)


In [30]:
y.nunique()

86

In [10]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(X, y_bin, test_size = 0.2)

In [11]:
max_len = 180
tok = Tokenizer(char_level=False,split=' ', lower=False)
tok.fit_on_texts(x_train)
sequences_train = tok.texts_to_sequences(x_train)

In [12]:
sequences_matrix_train = sequence.pad_sequences(sequences_train,maxlen=max_len)

In [13]:
sequences_test = tok.texts_to_sequences(x_test)
sequences_matrix_test = sequence.pad_sequences(sequences_test,
                                               maxlen=max_len)

In [14]:
sequences_train

[[4124,
  20,
  449,
  15,
  1065,
  216,
  424,
  25,
  252,
  29989,
  29989,
  6982,
  133,
  28,
  3661,
  192,
  1723,
  78,
  5715,
  404,
  8306,
  394,
  217,
  1826,
  18975,
  2003,
  27,
  39,
  2373,
  44236,
  540,
  1210,
  559,
  211,
  5715,
  404,
  44237,
  44238,
  44239,
  44240,
  3661,
  44241,
  133,
  183,
  2045,
  774,
  11,
  580,
  789,
  580,
  3088,
  647,
  157,
  6296,
  153,
  44242,
  728,
  2535,
  447,
  6076,
  1685,
  1685,
  687,
  265,
  468,
  54,
  396,
  545,
  1663,
  6,
  27,
  6982,
  133,
  28,
  3661,
  192,
  1723,
  1663,
  6,
  27,
  6982,
  133,
  28,
  3661,
  192,
  1723,
  1663,
  6,
  27,
  6982,
  133,
  28,
  3661,
  192,
  1723],
 [134,
  87,
  1860,
  16309,
  2637,
  1860,
  18976,
  1860,
  591,
  1860,
  71,
  178,
  93,
  5875,
  375,
  142,
  1860,
  149,
  18976,
  1860,
  30,
  1211,
  1860,
  1083,
  235,
  53,
  18976,
  1860,
  342,
  142,
  1860,
  149,
  85,
  44243,
  9279,
  190,
  1479,
  772,
  1,
  18976,
  18

In [15]:
sequences_test

[[41,
  2306,
  107,
  1695,
  16405,
  3035,
  793,
  1378,
  211,
  136,
  2504,
  762,
  2703,
  2808,
  1072,
  202,
  7347,
  919,
  3035,
  2137,
  2137,
  18064,
  2077,
  9294,
  93,
  99,
  164,
  107,
  1695,
  42,
  299,
  768,
  624,
  656,
  138,
  29,
  22,
  243,
  706,
  1056,
  790,
  4954,
  2808,
  1072,
  7347,
  2077,
  12,
  217,
  304,
  21,
  211,
  1734,
  649,
  5631,
  1868,
  217,
  30654,
  25273,
  95,
  1139,
  676,
  408,
  756,
  143,
  1173,
  211,
  762,
  115,
  13,
  2780,
  2137,
  185,
  75158,
  6905,
  1068,
  6905,
  2703,
  326,
  2849,
  168,
  2077,
  164,
  19,
  11756,
  217,
  5930,
  71,
  301,
  762,
  2703,
  630,
  2137,
  2808,
  1072,
  768,
  217,
  411,
  644,
  316,
  2808,
  6,
  6,
  1072,
  762,
  2703,
  316,
  2808,
  6,
  6,
  1072,
  762,
  2703,
  316,
  2808,
  6,
  6,
  1072,
  762,
  2703],
 [19,
  5,
  271,
  2936,
  705,
  64,
  295,
  16,
  164,
  745,
  242,
  114,
  1868,
  22,
  344,
  117,
  13,
  466,
  164,
  

In [16]:
tok.index_word

{1: 'android',
 2: 'java',
 3: '0',
 4: '1',
 5: 'using',
 6: 'c',
 7: 'string',
 8: 'class',
 9: 'get',
 10: 'code',
 11: 'new',
 12: 'file',
 13: 'use',
 14: 'function',
 15: '2',
 16: 'like',
 17: 'return',
 18: 'public',
 19: "i'm",
 20: 'error',
 21: 'this',
 22: 'way',
 23: 'int',
 24: 'method',
 25: 'data',
 26: 'app',
 27: 'object',
 28: 'value',
 29: 'would',
 30: 'want',
 31: '3',
 32: 'one',
 33: 'work',
 34: 'python',
 35: 'id',
 36: 'list',
 37: 'name',
 38: 'type',
 39: 'set',
 40: 'com',
 41: 'need',
 42: 'i',
 43: 'view',
 44: 'array',
 45: 'application',
 46: 'void',
 47: 'user',
 48: 'javascript',
 49: 'time',
 50: '4',
 51: 'test',
 52: 'e',
 53: 'example',
 54: 'know',
 55: 'system',
 56: 'php',
 57: 'a',
 58: 'text',
 59: 'jquery',
 60: 'var',
 61: 'x',
 62: 'html',
 63: 'line',
 64: 'image',
 65: 'layout',
 66: '5',
 67: 'make',
 68: 'div',
 69: 'run',
 70: 'add',
 71: 'problem',
 72: 'call',
 73: "i've",
 74: 'following',
 75: 'null',
 76: 'something',
 77: 'stat

In [17]:
vocab_len=len(tok.index_word.keys())

In [221]:
vocab_len

233227

In [222]:
sequences_matrix_train

array([[     0,      0,      0, ...,    105,   2434,   1981],
       [     0,      0,      0, ...,   1965,    297,    802],
       [     0,      0,      0, ...,   3815,    357,    736],
       ...,
       [     0,      0,      0, ...,   1445,     10,    295],
       [     0,      0,      0, ...,    424,    802,   1108],
       [     0,      0,      0, ...,  14185, 233227,    686]])

In [223]:
sequences_matrix_test

array([[    0,     0,     0, ...,    52,  4586,   727],
       [    0,     0,     0, ...,    11,   263,   297],
       [    0,     0,     0, ...,   442,   353,  2360],
       ...,
       [    0,     0,     0, ...,    28,  2337,   265],
       [    0,     0,     0, ...,   182,     9,   817],
       [    0,     0,     0, ...,    43,     3, 26656]])

In [22]:
def RNN():
    inputs = Input(name='inputs',shape=[max_len])
    layer = Embedding(vocab_len+1,500,input_length=max_len,mask_zero=True)(inputs)
    layer = LSTM(10)(layer)
    layer = Dense(100,name='FC1')(layer)
    layer = Activation('relu')(layer)
    layer = Dropout(0.5)(layer)
    layer = Dense(26,name='out_layer')(layer)
    layer = Activation('softmax')(layer)
    model = Model(inputs=inputs,outputs=layer)
    return model

In [23]:
es = EarlyStopping(patience=4)

In [24]:
model = RNN()
model.summary()
model.compile(loss='categorical_crossentropy',optimizer='adam',
              metrics=['accuracy'])

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
inputs (InputLayer)          (None, 180)               0         
_________________________________________________________________
embedding_2 (Embedding)      (None, 180, 500)          45153500  
_________________________________________________________________
lstm_2 (LSTM)                (None, 10)                20440     
_________________________________________________________________
FC1 (Dense)                  (None, 100)               1100      
_________________________________________________________________
activation_3 (Activation)    (None, 100)               0         
_________________________________________________________________
dropout_2 (Dropout)          (None, 100)               0         
_________________________________________________________________
out_layer (Dense)            (None, 26)                2626      
__________

In [26]:
model.fit(sequences_matrix_train,y_train,batch_size=150,epochs=50,validation_data=(sequences_matrix_test,y_test), callbacks=[es])

Train on 14317 samples, validate on 3580 samples
Epoch 1/50
14317/14317 [==============================] - 89s 6ms/step - loss: 17.9891 - acc: 0.1524 - val_loss: 19.6564 - val_acc: 0.1891
Epoch 2/50
14317/14317 [==============================] - 90s 6ms/step - loss: 17.9261 - acc: 0.1525 - val_loss: 19.5530 - val_acc: 0.1254
Epoch 3/50
14317/14317 [==============================] - 90s 6ms/step - loss: 17.6942 - acc: 0.1542 - val_loss: 19.6375 - val_acc: 0.1148
Epoch 4/50
14317/14317 [==============================] - 92s 6ms/step - loss: 17.5410 - acc: 0.1557 - val_loss: 19.7939 - val_acc: 0.1746
Epoch 5/50
14317/14317 [==============================] - 93s 6ms/step - loss: 17.4487 - acc: 0.1579 - val_loss: 20.0761 - val_acc: 0.2397
Epoch 6/50
14317/14317 [==============================] - 94s 7ms/step - loss: 17.3547 - acc: 0.1502 - val_loss: 20.2246 - val_acc: 0.0975
